In [8]:
import requests as rs
from zipfile import ZipFile
from io import BytesIO
import pandas as pd
from azure.storage.blob import ContainerClient,BlobServiceClient
from io import StringIO
import numpy as np
import json
import datetime as dt
import warnings
import duckdb as db
import time

# Set display options

pd.set_option('max_colwidth', None)

warnings.filterwarnings('ignore')

pd.set_option('display.max_columns', None)

pd.set_option('display.max_rows', None)

cxn = db.connect('../DB/dbfile')

print( 'connected to Db')
time.sleep(1)

# Parse Secrets

try:
    secrets = json.load(open(file='../secrets.json'))
    print('Secrets file found.')
except:
    print('Secrets file not found or some error in file. Make sure the file exists in the same directory as the code.')

if secrets:
    refresh_token = secrets['refresh_token']

    app_id = secrets['app_id']

    app_secret = secrets['app_secret']

    request_body = {
            "grant_type": "refresh_token",
            "refresh_token": refresh_token,
            "scope": "openid",
            "resource": "https://api.partnercenter.microsoft.com",
            "client_id": app_id,
            "client_secret": app_secret,
        }

    base_url = (
    'https://api.partnercenter.microsoft.com'
    )


    isAccessTokenObtained = 0


try:
    req = rs.post(
                "https://login.windows.net/6e75cca6-47f0-47a3-a928-9d5315750bd9/oauth2/token"
                ,data = request_body)
    
    access_token = json.loads(req.text)['access_token']
    isAccessTokenObtained = 1
    print('Refresh Token valid, access token obtained. \nAccess token : ',access_token[:20]+'...')
except:
    print('Refresh token expired, or no internet connection. \nUnable to obtain access token')
    print(json.loads(req.text))
    

if isAccessTokenObtained == 1:
        
        HTTPheaders = {'Authorization': 'Bearer ' + access_token}


connected to Db
Secrets file found.
Refresh Token valid, access token obtained. 
Access token :  eyJ0eXAiOiJKV1QiLCJh...


In [9]:
def query(sqlString:str)->None:
    """
    pretty prints quck db output
    """
    try:
        return cxn.query(sqlString).show(max_width = 100000, max_rows = 100000)
    except Exception as e:
        return e


In [10]:
def getInvoices()-> dict:
    
    try:
        relativeInvoicesURL = '/v1/invoices'
        response = json.loads(
        rs.get(
            f"{base_url}{relativeInvoicesURL}",
            headers=HTTPheaders)
        .content)

        return response['items']
    
    except Exception as e:
        return e

In [11]:
def updateInvoicesTbl()->None:
    """
    Updates the invoices table with the latest invoice data.
    """
    df = pd.DataFrame(getInvoices())
    cxn.query(f"TRUNCATE TABLE invoices; insert into invoices select * from df")

In [12]:
def getOneTimeInvoiceLineItems(invoiceID:str)->dict:
    
    try:
        newCommerceOneTimeBillingURL = f'/v1/invoices/OneTime-{invoiceID}/lineitems/OneTime/BillingLineItems?size=5000'

        response = json.loads(
            rs.get(
                    f"{base_url}{newCommerceOneTimeBillingURL}",
                    headers=HTTPheaders)
            .content) if rs.get(
                    f"{base_url}{newCommerceOneTimeBillingURL}",
                    headers=HTTPheaders).status_code == 200 else None # if response status code = 200
        
        return response['items']
    
    except Exception as e:
        return e

In [13]:
def writeOneTimeInvoiceLineItemsToDB(invoiceID:str,invoiceDate:str)->None:
    import pandas as pd
    df = pd.DataFrame(getOneTimeInvoiceLineItems(invoiceID))
    df['invoiceMonth'] = invoiceDate[:10]  # extract datetime string till date part
    destTbl:str = 'onetime'
    createQry:str = f"create table {destTbl} as select * from df"
    insertQry:str = f"insert into {destTbl} select * from df"
    try:
        cxn.query(createQry)
    except: # if tbl already exists
        cxn.query(insertQry)


In [14]:
dict = cxn.query("select id,billingperiodstartdate from invoices where id like 'G%' and totalcharges >0 and invoicedate >= '2022-05-06 00:00:00' order by invoicedate ").to_df().to_dict(orient='records')
dict

[{'id': 'G010313917', 'billingPeriodStartDate': '2022-04-01T00:00:00Z'},
 {'id': 'G011158456', 'billingPeriodStartDate': '2022-05-01T00:00:00Z'},
 {'id': 'G012066773', 'billingPeriodStartDate': '2022-06-01T00:00:00Z'},
 {'id': 'G013015192', 'billingPeriodStartDate': '2022-07-01T00:00:00Z'},
 {'id': 'G013892461', 'billingPeriodStartDate': '2022-08-01T00:00:00Z'},
 {'id': 'G014912221', 'billingPeriodStartDate': '2022-09-01T00:00:00Z'},
 {'id': 'G015890617', 'billingPeriodStartDate': '2022-10-01T00:00:00Z'},
 {'id': 'G016909819', 'billingPeriodStartDate': '2022-11-01T00:00:00Z'},
 {'id': 'G017943686', 'billingPeriodStartDate': '2022-12-01T00:00:00Z'},
 {'id': 'G018993861', 'billingPeriodStartDate': '2023-01-01T00:00:00Z'},
 {'id': 'G020077203', 'billingPeriodStartDate': '2023-02-01T00:00:00Z'},
 {'id': 'G021249609', 'billingPeriodStartDate': '2023-03-01T00:00:00Z'},
 {'id': 'G022498969', 'billingPeriodStartDate': '2023-04-01T00:00:00Z'},
 {'id': 'G023804626', 'billingPeriodStartDate': '20

In [17]:
#convert this str to date
for element in dict:
    print(element['billingPeriodStartDate'][:10])

2022-04-01
2022-05-01
2022-06-01
2022-07-01
2022-08-01
2022-09-01
2022-10-01
2022-11-01
2022-12-01
2023-01-01
2023-02-01
2023-03-01
2023-04-01
2023-05-01
2023-06-01
2023-07-01
2023-08-01
2023-09-01
2023-10-01
2023-11-01
2023-12-01
2024-01-01
2024-02-01


In [18]:
# cxn.query('truncate table onetime')
# for element in dict:
#     df = pd.DataFrame(getOneTimeInvoiceLineItems(element['id']))
#     df['invoiceMonth'] = element['billingPeriodStartDate'][:10]
#     df.to_parquet(f'../DB/onetime_invoices/{element["id"]}_{element['billingPeriodStartDate'][:10]}.parquet', compression='gzip', index=False)
    


In [21]:
cxn.query(""" 
          select customerid,customername,skuname,subscriptionid,subscriptionstartdate,invoicemonth,sum(subtotal) total  from read_parquet('../DB/onetime_invoices/*.parquet')
       where productid like 'CFQ%' and invoicemonth >= '2023-04-01'
         --  group by customerid,customername,skuname,invoicemonth 
          order by invoicemonth,customerid,customername,skuname
      
          """)
# .to_csv('../OfficeCost.csv')

BinderException: Binder Error: column "customerid" must appear in the GROUP BY clause or must be part of an aggregate function.
Either add it to the GROUP BY list, or use "ANY_VALUE(customerid)" if the exact value of "customerid" is not important.

In [41]:
cxn.query(f""" drop table onetime;
          create table onetime as select {requiredColumns}
      from read_parquet('../DB/onetime_invoices/*.parquet')
       where productid like 'CFQ%' and invoicemonth >= '2023-04-01'
      --and customername like '%Annet%'
         --  group by customerid,customername,skuname,invoicemonth 
          order by customerid,customername,skuname,invoicemonth
      
      
          """)

In [42]:
cxn.query("select * from onetime")

┌──────────────────────┬──────────────────────┬──────────────────────┬───┬──────────────────────┬──────────────┐
│      customerId      │     customerName     │  customerDomainName  │ … │ subscriptionEndDate  │      mn      │
│       varchar        │       varchar        │       varchar        │   │       varchar        │   varchar    │
├──────────────────────┼──────────────────────┼──────────────────────┼───┼──────────────────────┼──────────────┤
│ 0052d4df-9e92-4ca5…  │ Henceworth Technol…  │ henceworthtechnolo…  │ … │ 2024-01-19T00:00:00Z │ January2023  │
│ 0052d4df-9e92-4ca5…  │ Henceworth Technol…  │ henceworthtechnolo…  │ … │ 2024-01-19T00:00:00Z │ January2023  │
│ 0052d4df-9e92-4ca5…  │ Henceworth Technol…  │ henceworthtechnolo…  │ … │ 2024-01-19T00:00:00Z │ January2023  │
│ 0052d4df-9e92-4ca5…  │ Henceworth Technol…  │ henceworthtechnolo…  │ … │ 2024-01-19T00:00:00Z │ January2023  │
│ 0052d4df-9e92-4ca5…  │ Henceworth Technol…  │ henceworthtechnolo…  │ … │ 2024-01-19T00:00:00Z 

In [21]:
query(""" 
          select * from read_parquet('../DB/onetime_invoices/*.parquet')
       where productid like 'CFQ%' and
          customerId = '00a9ff8c-9830-4847-ae51-4579ec092cb4' and skuname = 'Exchange Online Archiving for Exchange Online'
and invoiceMonth = '2023-06-01'
      
          """)

┌──────────────────────────────────────┬──────────────────────────────────────┬───────────────────────────────────────────────┬───────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬──────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬───────────────────────────────────────────────┬───────────────────────────────────────────────┬───────────────────┬────────────┬───────────┬────────────────────┬──────────┬──────────┬──────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬──────────────────────┬──────────────────────┬────────────────────────────────────────────────┬──────────────┬──────────────────────────────────────┬─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┬─────────────────┬─────────────────┬───────────────

In [29]:
query(r"""
select * from read_csv("C:\Users\MohammedSafiAhmed\Downloads\OfficeInvoice_January2024 - InvoiceLineItems.csv")
          where "CP ID" = 8707 and "Item Name" like '%Exchange Online%'

""")

┌───────┬──────────────────────────────────────┬────────────────┬────────────┬─────────┬───────────────────────────────────────────────┬──────────────────────────────────────────────────────────────────────────────────────────┬──────────┬────────────┐
│ CP ID │             Microsoft Id             │ Invoice Number │ Order Date │ Item Id │                   Item Name                   │                                     Item Description                                     │ Quantity │ Unit Price │
│ int64 │               varchar                │     int64      │    date    │  int64  │                    varchar                    │                                         varchar                                          │  int64   │   double   │
├───────┼──────────────────────────────────────┼────────────────┼────────────┼─────────┼───────────────────────────────────────────────┼──────────────────────────────────────────────────────────────────────────────────────────┼──────────┼──────

connected to Db
Secrets file found.
Refresh Token valid, access token obtained. 
Access token :  eyJ0eXAiOiJKV1QiLCJh...


In [14]:
cxn.query("Select count(distinct(concat(customername,customerid,invoicemonth))) from read_csv('../Officecost.csv')")

┌────────────────────────────────────────────────────────────────┐
│ count(DISTINCT concat(customername, customerid, invoicemonth)) │
│                             int64                              │
├────────────────────────────────────────────────────────────────┤
│                                                           9737 │
└────────────────────────────────────────────────────────────────┘

In [8]:
query("select * from read_parquet('../DB/onetime_invoices/February_2024.parquet') where productid like 'CFQ%' limit 10")

┌──────────────────────────────────────┬──────────────────────────────────────┬───────────────────────────────────────────────┬─────────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬──────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬─────────────────────────────────┬─────────────────────────────────┬───────────────────┬─────────────┬───────────┬────────────────────┬──────────┬──────────┬───────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬───────────────────────┬──────────────────────┬──────────────────────────────┬──────────────────────┬────────────────────────────────────────────────┬──────────────┬──────────────────────────────────────┬─────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┬─────────────────┬──

In [17]:
cxn.query("select customername,customerid,skuname,invoicemonth,round(sum(subtotal),2) Amount from onetime where productid like 'CFQ%' group by customername,customerid,skuname,invoicemonth order by 1,2,3").to_csv('../OfficeCost.csv')

In [33]:
df = cxn.query("select * from invoices where id like 'G%' and invoicedate >= '2023-01-07T00:00:12.4144899Z'").to_df()
# display(df.head(2))
idMapping:dict = df[['id','invoiceDate']].to_dict(orient='records')
idMapping


[{'id': 'G018993861', 'invoiceDate': '2023-02-06T01:59:16.4888139Z'},
 {'id': 'G020077203', 'invoiceDate': '2023-03-06T02:19:06.3710451Z'},
 {'id': 'G021249609', 'invoiceDate': '2023-04-06T03:00:28.1147298Z'},
 {'id': 'G022498969', 'invoiceDate': '2023-05-07T04:29:12.4144899Z'},
 {'id': 'G023804626', 'invoiceDate': '2023-06-06T01:59:42.3923502Z'},
 {'id': 'G025172256', 'invoiceDate': '2023-07-06T02:50:41.272832Z'},
 {'id': 'G026628959', 'invoiceDate': '2023-08-06T04:51:20.6160137Z'},
 {'id': 'G028190160', 'invoiceDate': '2023-09-06T02:55:09.7438877Z'},
 {'id': 'G029930588', 'invoiceDate': '2023-10-06T04:03:02.9922945Z'},
 {'id': 'G031809747', 'invoiceDate': '2023-11-06T06:12:49.3152717Z'},
 {'id': 'G033956933', 'invoiceDate': '2023-12-06T04:54:24.6700292Z'},
 {'id': 'G036230777', 'invoiceDate': '2024-01-06T04:38:53.4719149Z'},
 {'id': 'G038562576', 'invoiceDate': '2024-02-06T02:22:09.3731752Z'},
 {'id': 'G041051163', 'invoiceDate': '2024-03-06T04:00:40.8516225Z'}]

In [34]:
df = pd.DataFrame(getOneTimeInvoiceLineItems('G041051163'))
df['invoiceMonth'] = 'February_2024'
query('select * from df limit 3')

┌──────────────────────────────────────┬──────────────────────────────────────┬────────────────────────────────────┬────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬──────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬──────────────────────────────┬──────────────────────────────┬───────────────────┬─────────────┬───────────┬────────────────────┬──────────┬──────────┬──────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬───────────────────────┬──────────────────────┬──────────────────────────────┬──────────────────────┬────────────────────────────────────────────────┬──────────────┬──────────────────────────────────────┬────────────────────────────┬─────────────────┬─────────────────┬────────────────────┬────────────────────────┬──────────────────┬──────────────────┬──────────────────┬─────────────────────────────────────

In [35]:
df.to_parquet('../DB/onetime_invoices/February_2024.parquet')

In [36]:
cxn.query("truncate table onetime")

In [38]:
# cxn.query("insert into onetime select * from read_parquet('../DB/onetime_invoices/*_2024.parquet') ")

In [44]:
query("select customerid from onetime where productid like 'CFQ%'  and orderdate >= '2023-04-01T00:00:00' ")

┌──────────────────────────────────────┬──────────────────────────────────────┬─────────────────────────────────────┬────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬──────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬──────────────────────────────┬──────────────────────────────┬───────────────────┬─────────────┬───────────┬────────────────────┬──────────┬──────────┬──────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬───────────────────────┬──────────────────────┬──────────────────────────────┬──────────────────────┬────────────────────────────────────────────────┬──────────────┬──────────────────────────────────────┬────────────────────────────┬─────────────────┬─────────────────┬────────────────────┬────────────────────────┬──────────────────┬──────────────────┬──────────────────┬────────────────────────────────────

In [16]:
cxn.query(r"select * from read_csv('C:\Users\MohammedSafiAhmed\Downloads\OfficeInvoice_January2024 - InvoiceLineItems.csv')").to_csv('../OfficeSale.csv')


In [134]:
cxn.query("""

with onetimecte as (
      select customerid,skuname, sum(subtotal) subtotalCost, sum(totalforcustomer) totalforcustomerCost
      from  onetime where productid like 'CFQ%'  and orderdate >= '2023-04-01T00:00:00' 
      group by customerid,skuname
)
      ,
      hareeshcte as (
      select "cp id","microsoft id","item name", sum(Quantity*"unit price") totalSale from hareeshData
      group by 1,2,3

      )
      ,
      final as 
      (select a."cp id",a."microsoft id",b.customerid,b.skuname,a."item name",b.subtotalCost,b.totalforcustomerCost,a.totalSale,ifnull(a.totalsale,0)-b.subtotalcost margin
       from hareeshcte a full join onetimecte b on a."microsoft id" = b.customerid and a."item name" = b.skuname
          
          )
      ,
          final1 as 
          (
          select * from final b left join (with a as (select distinct customerid,customername from onetime where productid like 'CFQ%' and orderdate >= '2023-04-01 00:00:00' order by 1,2)
      ,
      b as (
      select customerid,string_agg(customername,',') as customername from a group by 1
      )select * from b) c
          on b.customerid = c.customerid
          ),
      final2 as 
          (select "CP ID","Microsoft Id",customerid,customername,skuname,round(subtotalCost,2) subtotalCost,round(totalforcustomerCost,2)totalforcustomerCost,
      round(totalSale,2)totalSale,round(margin,2) margin from final1
      order by margin )
      select * from final2 order by ifnull("cp id",-1) ,margin



""")\
.to_csv('../safi.csv')

In [103]:
for dict in idMapping:
    if dict['id'] not in ('G022498969','G018993861','G025172256','G020077203','G021249609','G023804626'):
        try:
            writeOneTimeInvoiceLineItemsToDB(dict['id'],dict['invoiceDate'])
            print(f"written data for invoiceid: {dict['id']}")
        except:
            print(f"failed to write data for invoiceid: {dict['id']}")

failed to write data for invoiceid: G026628959
written data for invoiceid: G028190160
failed to write data for invoiceid: G029930588
failed to write data for invoiceid: G031809747
written data for invoiceid: G033956933
failed to write data for invoiceid: G036230777


In [8]:
latestInvoice = cxn.query("select id from invoices where id like 'G%' order by invoicedate desc limit 1 ")
latestInvoice = str(latestInvoice).replace("┌────────────┐\n│     id     │\n│  varchar   │\n├────────────┤\n│ ",'').replace(" │\n└────────────┘\n",'')
latestInvoice

'G038562576'

In [9]:
previousInvoice = cxn.query("select id from invoices where id like 'G%' order by invoicedate  desc limit 1 offset 1 ")
previousInvoice = str(previousInvoice).replace("┌────────────┐\n│     id     │\n│  varchar   │\n├────────────┤\n│ ",'').replace(" │\n└────────────┘\n",'')
previousInvoice

'G036230777'

In [10]:
latestMonthDF = pd.DataFrame(getOneTimeInvoiceLineItems(latestInvoice))


In [26]:
query('select * from onetime limit 10')

┌──────────────────────────────────────┬──────────────────────────────────────┬─────────────────────────────────────────────┬─────────────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬──────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬─────────────────────────────────┬─────────────────────────────────┬───────────────────┬─────────────┬───────────┬────────────────────┬──────────┬──────────┬──────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬───────────────────────┬──────────────────────┬──────────────────────────────┬──────────────────────┬────────────────────────────────────────────────┬──────────────┬──────────────────────────────────────┬────────────────────────────┬─────────────────┬─────────────────┬────────────────────┬────────────────────────┬──────────────────┬──────────────────┬──────────────────┬─────────────

In [11]:
query("select * from latestMonthDF where productid not like 'CFQ%' order by customerdomainname")

┌──────────────────────────────────────┬──────────────────────────────────────┬─────────────────────────────────────────────────┬────────────────────────────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬───────────────────────────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬───────────────────────────────────────────────────────────────────────────────┬───────────────────────────────────────────────────────────────────────────────────────────────────────────┬───────────────────┬─────────────┬────────────┬────────────────────┬──────────────┬──────────┬───────────┬──────────┬──────────────────┬──────────┬───────────────────────┬─────────────┬──────────────────────────────────────────────────────────────────────────────────────┬──────────────────────────────────────┬───────────────────────┬──────────────────────┬──────────────────────┬──────────────────────────────┬─────────────────────────────────────────────────────────

In [8]:
previousMonthDF = pd.DataFrame(getOneTimeInvoiceLineItems(previousInvoice))
previousMonthDF.head()

partnerId                            customerId  \
0  6e75cca6-47f0-47a3-a928-9d5315750bd9  d4815a57-d729-404d-acf8-c4da4e8b875a   
1  6e75cca6-47f0-47a3-a928-9d5315750bd9  b05d8285-01a8-496a-9ee6-b0440e69121c   
2  6e75cca6-47f0-47a3-a928-9d5315750bd9  07782621-ac3c-431b-b38a-b596b49956c0   
3  6e75cca6-47f0-47a3-a928-9d5315750bd9  b04c2da1-cb08-4b2a-9099-51b492037918   
4  6e75cca6-47f0-47a3-a928-9d5315750bd9  76d5d933-2ddc-40cb-a89f-0c4cd5964319   

                          customerName                  customerDomainName  \
0               Tata Chemicals Limited                   tatachemicals.net   
1       Aapkapainter Solutions Pvt Ltd  anupamaapkapainter.onmicrosoft.com   
2                           briodevptm          briodevptm.onmicrosoft.com   
3  Intelogixs Research Private Limited                      intelogixs.com   
4              Synthesis Solutions LLP             synthesis-solutions.com   

  customerCountry invoiceNumber    mpnId  resellerMpnId  \
0              IN    G036230777  2240443              0   
1              IN    G036230777  2240443              0   
2              IN    G036230777  2240443              0   
3              IN    G036230777  2240443              0   
4              IN    G036230777  2240443              0   

                             orderId                     orderDate  \
0  tUvDFTHutf0yA_Q0KT_zQYVKFn2K6yM31   2024-01-03T21:21:09.949796Z   
1  9TU9-mcxSXgpz5ymp720QZ29Op25EUio1  2024-01-03T18:17:05.0117523Z   
2  K0VAxK9tfbZ7ptkHTim5T73od_vhVuSL1  2024-01-03T19:55:59.5947268Z   
3  mNvOalIJyqULGlcHqpQBTZ5mKqwTN1pm1  2024-01-03T19:38:06.5629395Z   
4  KOpgQtyqwPCrlJDVcT0bQ6gUsyZaMjtg1  2024-01-03T17:37:32.4806528Z   

      productId skuId availabilityId                 productName  \
0  DZH318Z0BNX0  0021   DZH318Z09T1W                   Azure DNS   
1  DZH318Z0BP05  006J   DZH318Z0GM03                      Backup   
2  DZH318Z0BNZH  006F   DZH318Z0QCXV          General Block Blob   
3  DZH318Z0BP0L  00C4   DZH318Z0L2LH  Standard HDD Managed Disks   
4  DZH318Z0BP0L  018G   DZH318Z0LC7V  Standard HDD Managed Disks   

                                          skuName productQualifiers  \
0                             Azure DNS - Private                []   
1                     Backup - Standard - US East                []   
2                        General Block Blob - LRS                []   
3  Standard HDD Managed Disks - S10 LRS - US East                []   
4             Standard HDD Managed Disks - S4 LRS                []   

  chargeType  unitPrice  effectiveUnitPrice    unitType  quantity  subtotal  \
0        new    0.50000            0.425000           1         1    176.68   
1        new    0.04480            0.038080  1 GB/Month         1    105.84   
2        new    0.00036            0.000306         10K         1      0.00   
3        new    5.88800            5.004800     1/Month         1   3652.95   
4        new    0.00050            0.000425         10K         1     76.67   

   taxTotal  totalForCustomer currency publisherName publisherId  \
0     31.80            208.48      INR     Microsoft               
1     19.05            124.89      INR     Microsoft               
2      0.00              0.00      INR     Microsoft               
3    657.53           4310.48      INR     Microsoft               
4     13.80             90.47      INR     Microsoft               

  subscriptionDescription                        subscriptionId  \
0              Azure plan  392186e1-5981-4d72-c052-adfbb3645f4c   
1              Azure plan  9ef9ff61-dbdd-4fbc-de83-def3ef5f6c4a   
2              Azure plan  b68b5c74-15d1-4edb-c5c4-5261052d03c6   
3              Azure plan  22b7da32-0ed2-4df4-d549-4137ba6afe95   
4              Azure plan  e1aef069-f8cd-5c29-5be6-5e2de00a2f3a   

        chargeStartDate         chargeEndDate  \
0  2023-12-01T00:00:00Z  2023-12-31T23:59:59Z   
1  2023-12-01T00:00:00Z  2023-12-31T23:59:59Z   
2  2023-12-01T00:00:00Z  202

In [134]:
query("select * from latestTbL")

┌───────────────────────────────────────┬──────────────────────────────┬──────────────────────────────────────┬──────────────────────────┬──────────────────────┬─────────────────┬────────────────────┬──────────────────┬──────────────────┬───────────┐
│          customerDomainName           │          orderDate           │            subscriptionId            │ truncatedchargestartdate │    chargeEndDate     │   chargeType    │ effectiveUnitPrice │ billableQuantity │ totalForCustomer │   mName   │
│                varchar                │           varchar            │               varchar                │           date           │       varchar        │     varchar     │       double       │      double      │      double      │  varchar  │
├───────────────────────────────────────┼──────────────────────────────┼──────────────────────────────────────┼──────────────────────────┼──────────────────────┼─────────────────┼────────────────────┼──────────────────┼──────────────────┼─────────

In [36]:
# cxn.query('drop table onetime')

In [37]:
requiredColumns = """
 customerId,
 customerName,
 customerDomainName,
 invoiceNumber,
 orderDate,
 invoiceNumber,
 substring(skuName,0,30) skuName,
 skuid,
 productname,
 subscriptionId,
 chargeType,
 effectiveUnitPrice,
 quantity,
 subtotal,
 taxTotal,
 totalForCustomer,
 chargeStartDate,
 chargeEndDate,
 referenceId,
 billableQuantity,
 invoiceMonth,
 subscriptionStartDate,
 subscriptionEndDate,
 monthname(cast(subscriptionstartdate as datetime)) || cast(year(cast(subscriptionstartdate as datetime))as varchar) as  mn
 """ # concat monthname and year

# raw

In [35]:
query(f"""
      --
      with t0 as 
      (select {requiredColumns}
      from onetime 
      where 
      productid like 'CFQ%'
      --and customerDomainName = 'yaxiso365.onmicrosoft.com'
      and customerDomainName = 'annet50.onmicrosoft.com'
       
       --and subscriptionId = 'cd963bd4-ada7-4235-c211-0f926c3a7b87'
       order by subscriptionid, orderdate)

       ,

       t1 as 

      (select customerdomainname,subscriptionid,round(sum(totalforcustomer)) sm from t0
       group by 1,2 order by 3 desc)

       select * from t0
       """)

┌────────────┬──────────────┬────────────────────┬───────────────┬───────────┬─────────────────┬─────────┬─────────┬─────────────┬────────────────┬────────────┬────────────────────┬──────────┬──────────┬──────────┬──────────────────┬─────────────────┬───────────────┬─────────────┬──────────────────┬──────────────┬───────────────────────┬─────────────────────┬─────────┐
│ customerId │ customerName │ customerDomainName │ invoiceNumber │ orderDate │ invoiceNumber_1 │ skuName │  skuId  │ productName │ subscriptionId │ chargeType │ effectiveUnitPrice │ quantity │ subtotal │ taxTotal │ totalForCustomer │ chargeStartDate │ chargeEndDate │ referenceId │ billableQuantity │ invoiceMonth │ subscriptionStartDate │ subscriptionEndDate │   mn    │
│  varchar   │   varchar    │      varchar       │    varchar    │  varchar  │     varchar     │ varchar │ varchar │   varchar   │    varchar     │  varchar   │       double       │  int64   │  double  │  double  │      double      │     varchar     │    v

# Transformed

In [238]:
query(f"""
 
with 
      t0 as (
      select {requiredColumns}
      from onetime 
      --where productid like 'CFQ%'  
      --and customerDomainName = 'yaxiso365.onmicrosoft.com'
      --and customerDomainName = 'annet50.onmicrosoft.com'
      --and subscriptionid = '12266bbd-6d4a-422f-d413-4c688cc48550'
      )
      ,
     
      t1 as                                            /* club rows that have similar charge types and reference IDs. */

      (select customername,customerid,customerdomainname,skuname,skuid,productname,max(cast(orderDate as datetime)) orderdate1
      ,last(invoicenumber order by orderdate) newInvoiceNumber
      ,subscriptionid,date_trunc('day',cast(chargestartdate as datetime)) truncatedchargestartdate
      , chargeenddate,chargetype
      ,first(billablequantity order by totalforcustomer desc) fbqty , last(billablequantity order by totalforcustomer desc) lbqty
      ,fbqty - lbqty QtyAdded
      ,case when qtyadded = 0 then fbqty else qtyadded end as QtyAdded_adjusted
      ,round(sum(totalforcustomer),2) newTotal
      ,case when newTotal < 0 then -(abs(QtyAdded_adjusted)) else QtyAdded_adjusted end as QtyAdded_adjustedForNegativity
      ,referenceid
      ,mn
      from t0  
      group by customername,customerid,customerdomainname,subscriptionid,skuname,skuid,productname,truncatedchargestartdate, chargeenddate,chargetype,referenceid,mn
      order by subscriptionid,orderdate1)
      
      ,

       t2 as

       (select *
      ,sum(QtyAdded_adjustedForNegativity) over(partition by customerid,customerdomainname, subscriptionid, mn ,cast(chargeenddate as date) order by orderdate1 rows between unbounded preceding and  0 following) as finalLicenseQty
      ,truncatedchargestartdate newSDate
      , lead(truncatedchargestartdate) over(partition by customerid, customerdomainname,subscriptionid,mn order by orderdate1 ) adjustedChargeStartDate 
      ,case when adjustedChargeStartDate is null then date_add(cast(chargeenddate as date), interval 1 day) 
      else adjustedChargeStartDate end as  lead_adjustedChargeStartDate,
       from t1
        order by subscriptionid,orderdate1 )
      
      ,

      subscriptionWiseBreakdown as
       
         (select customerid,customerdomainname,subscriptionid,round(sum(newTotal),2) sm from t2 group by 1,2,3 order by 4 desc)
      
      ,

      final as 
      (
      select customername,customerid,customerDomainName,newInvoiceNumber as invoiceId,orderDate1 orderDate,subscriptionId,skuname,skuid,productname,newSdate as chargeStartDate,
      case when chargestartdate = lead_adjustedChargeStartDate then cast(lead_adjustedChargeStartDate as date) else cast(lead_adjustedChargeStartDate as date)-1 end as chargeEndDate,chargeType, finalLicenseQty Qty, newTotal Amount
      --, mn billingMonth
      from t2
      order by subscriptionid,orderdate
      )
      /*,
      getInvoiceDate as (
      select * from final a join invoices

      )
      */
      ,
      tn1 as 
      (select * from (select * from tn4
      --where customername like '%Annet%'
      --and skuname = 'Microsoft 365 Business Standa'
      order by subscriptionid,chargestartdate, chargeenddate) a 
      join 
      (select cast(unnest(generate_series(date '2023-04-01', date '2024-04-01', INTERVAL '1 day')) as date) as days) b
      on b.days between a.chargestartdate and a.chargeenddate)
      ,
      tn4 as 
      (select *, sum(amount) over (partition by customername,customerid,customerdomainname,skuname,subscriptionid order by chargestartdate,chargeenddate,qty) rollingAmt,
       rollingamt / (cast(chargeenddate as date)+1  - cast(chargestartdate as date)) dailyPrice from final
      --where customername like '%Annet%'
      --and skuname = 'Microsoft 365 Business Standa'
      order by subscriptionid,chargestartdate, chargeenddate)
      ,
      tn5 as 
      (select customername,customerid,customerdomainname,skuname,days,sum(qty) qty, sum(dailyprice) amt
      
         from tn1 group by customername,customerid,customerdomainname,skuname,days order by days)
         ,
         tn6 as 
      (select *
       ,row_number() over(partition by customerdomainname,skuname,qty order by days) rn
       ,days-cast(rn as int) groupkey
      
        from tn5
         )
         ,
         tn7 as 
         (select customername,customerid,customerdomainname,skuname,min(days) start_date, max(days) end_date, max(qty) qty, round(sum(amt),2) amt
           from tn6
           group by customername,customerid,customerdomainname,skuname, groupkey
           order by 1,2,3,4,5,6)
           select * from tn7 



      
      
""")\
# .to_csv('../licensceQtyOverTime.csv')

┌────────────────────────────────────────────────────────────────┬──────────────────────────────────────┬───────────────────────────────────────┬───────────────────────────────┬────────────┬────────────┬────────┬─────────────┐
│                          customerName                          │              customerId              │          customerDomainName           │            skuName            │ start_date │  end_date  │  qty   │     amt     │
│                            varchar                             │               varchar                │                varchar                │            varchar            │    date    │    date    │ double │   double    │
├────────────────────────────────────────────────────────────────┼──────────────────────────────────────┼───────────────────────────────────────┼───────────────────────────────┼────────────┼────────────┼────────┼─────────────┤
│     Jupiter  Lifeline Hospital Ltd                             │ b0e0b885-4ecd-4b44-a47c-2

In [137]:
cxn.query("select cast(unnest(generate_series(date '2023-04-01', date '2024-03-31', INTERVAL '1 day')) as date) as days")

┌────────────┐
│    days    │
│    date    │
├────────────┤
│ 2023-04-01 │
│ 2023-04-02 │
│ 2023-04-03 │
│ 2023-04-04 │
│ 2023-04-05 │
│ 2023-04-06 │
│ 2023-04-07 │
│ 2023-04-08 │
│ 2023-04-09 │
│ 2023-04-10 │
│     ·      │
│     ·      │
│     ·      │
│ 2024-03-22 │
│ 2024-03-23 │
│ 2024-03-24 │
│ 2024-03-25 │
│ 2024-03-26 │
│ 2024-03-27 │
│ 2024-03-28 │
│ 2024-03-29 │
│ 2024-03-30 │
│ 2024-03-31 │
├────────────┤
│  366 rows  │
│ (20 shown) │
└────────────┘

In [321]:
query(f"""
      --select customerdomainname,subscriptionid,round(sum(tfc),2) sm from 
    --/*
       (select * exclude (qty,qtyadded,actualqty) , case when chargetype in ('moveQuantity','convert') and tfc <0 then -actualqty else actualqty end as actualqty1
      ,sum(actualqty1) over(partition by subscriptionid,mn order by orderdate rows between unbounded preceding and 0 following )totalqty
      ,truncatedchargestartdate newSDate
      ,case when lead(truncatedchargestartdate) over(partition by subscriptionid order by orderdate ) is null then chargeenddate 
      else lead(truncatedchargestartdate) over(partition by subscriptionid order by orderdate ) end as  newEDate,
       from 
      --*/
(select customerdomainname,max(orderdate) orderdate,subscriptionid,date_trunc('day',cast(chargestartdate as datetime)) truncatedchargestartdate
      , chargeenddate,chargetype
      ,first(effectiveUnitPrice order by effectiveUnitPrice desc) absEffectiveUnitPrice
      ,max(billablequantity) qty
      ,first(billablequantity order by effectiveUnitPrice desc) - last(billablequantity order by effectiveUnitPrice desc) QtyAdded,referenceid
      ,case when chargetype in ('addQuantity','removeQuantity','moveQuantity','convert','cycleCharge') then qtyadded else qty end as actualqty
      ,round(sum(totalforcustomer),2) tfc
      ,monthname(cast(subscriptionstartdate as datetime))||cast(year(cast(subscriptionstartdate as datetime))as varchar) mn
      from onetime 
      where 
      customerDomainName = 'annet50.onmicrosoft.com'
      --and 
      --subscriptionid = '12266bbd-6d4a-422f-d413-4c688cc48550'
      group by customerdomainname,subscriptionid,truncatedchargestartdate, chargeenddate,chargetype,referenceid,mn
      order by subscriptionid,orderdate)
      order by subscriptionid,orderdate)
      --group by 1,2 order by 3 desc
      

""")

┌─────────────────────────┬──────────────────────────────┬──────────────────────────────────────┬──────────────────────────┬──────────────────────┬────────────────┬───────────────────────┬──────────────────────────────────────┬───────────┬───────────────┬────────────┬──────────┬────────────┬──────────────────────┐
│   customerDomainName    │          orderdate           │            subscriptionId            │ truncatedchargestartdate │    chargeEndDate     │   chargeType   │ absEffectiveUnitPrice │             referenceId              │    tfc    │      mn       │ actualqty1 │ totalqty │  newSDate  │       newEDate       │
│         varchar         │           varchar            │               varchar                │           date           │       varchar        │    varchar     │        double         │               varchar                │  double   │    varchar    │   double   │  double  │    date    │       varchar        │
├─────────────────────────┼─────────────────────────

In [10]:
import duckdb as db
import pandas as pd


db.query("select * exclude(attributes,priceAdjustmentDescription,productQualifiers) from read_parquet('../DB/onetime_invoices/*') " ).show(max_width=100000, max_rows=10)



┌──────────────────────────────────────┬──────────────────────────────────────┬───────────────────────────────────────┬────────────────────────────────────┬─────────────────┬───────────────┬─────────┬───────────────┬───────────────────────────────────┬──────────────────────────────┬──────────────┬─────────┬────────────────┬──────────────────────────────┬─────────────────────────────────────────────────┬───────────────────┬────────────┬───────────┬────────────────────┬────────────┬──────────┬──────────┬──────────┬──────────────────┬──────────┬───────────────┬─────────────┬─────────────────────────┬──────────────────────────────────────┬──────────────────────┬──────────────────────┬────────────────────────────┬──────────────┬──────────────────────────────────────┬─────────────────┬─────────────────┬────────────────────┬────────────────────────┬──────────────────┬────────────────────────────────────────────────────────────────────┬──────────────────┬───────────────────────────────────────

In [24]:
import duckdb as db
import pandas as pd


df = db.query("select * exclude(attributes,priceAdjustmentDescription,productQualifiers)  from read_parquet('../NCE Recon Files/*',union_by_name=True) " ).to_df()


from azure.storage.filedatalake import (
    DataLakeServiceClient
)
import pandas as pd



def upload_to_adls(folder_name,file_name,dataframe):

    
    container = "reconfiles"
    storage_account_name = "briodatawarehouse"
    storage_account_key="4gD67IqpwAGRyMCh+b5MBqlqGuGPceEkJo1/YcvQcWvT0kSK/10Rq7A2hrat/JucWiAd4of62szR+AStoDNAXA=="
    service_client = DataLakeServiceClient(account_url="{}://{}.dfs.core.windows.net".format(
            "https", storage_account_name), credential=storage_account_key)
    file_system_client = service_client.get_file_system_client(file_system=container)

    directory_client=file_system_client.get_directory_client(folder_name)

    file_client=directory_client.get_file_client(file_name)

    data = dataframe.to_parquet( index = False)

    file_client.upload_data(data,overwrite=True)



upload_to_adls('raw_data',"nce.parquet",df)